# ToDo :

* ~~consolidate code from notebook into WISDM helper methods file~~
* rewrite kfolds process so that we have more precise control over the size of a fold (as oppose to just the number of folds)
* run experiment that directly compares model using ALL general data + active data to model using ONLY general data from nearest cluster + active data
* analyze/visualize clusters (is there a better algorithm? is there a better k for the k-means?) 
* perhaps compare with using the WORST cluster, or using ONLY the personal data
    * for each size of active data
        * for each algorithm (also ensemble algorithm?)
            * personal only
            * universal only
            * personal + ALL universal
            * personal + best cluster universal
            * personal + worst cluster universal


In [1]:
from wisdm import wisdm
import numpy as np
import pandas as pd

from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import StratifiedKFold, StratifiedShuffleSplit
from sklearn.cluster import KMeans
from scipy.stats import mode

In [2]:
# FIXING WISDM DATA SO IT CAN LOAD with loadarff()
with open("../../WISDM_at_v2.0/WISDM_at_v2.0_transformed.arff", "r") as fIn:
    old_lines = fIn.readlines()
    new_lines = []
    for ind, line in enumerate(old_lines):
        if ind is 2:
            brack_index = line.find("{")
            new_line = line[:bracket_index]
            new_line += line[bracket_index:].replace('"', '')
        elif ind is 46:
            bracket_index = line.find("{")
            new_line = line[:bracket_index]
            new_line += " "+line[bracket_index:].replace('"', '')
        else:
            new_line = line
        new_lines.append(new_line)

with open("../../WISDM_at_v2.0/WISDM_at_v2.0_transformed_FIXED.arff", "w") as fOut:
    for line in new_lines:
        fOut.write(line)     

In [77]:
wisdm.set_data()

In [2]:
import importlib
importlib.reload(wisdm)

<module 'wisdm.wisdm' from '/Users/scottcambo/Documents/grad_school/SegalProject/WISDM/wisdm/wisdm.py'>

# Test Universal Impersonal Model Pipeline

In [78]:
import warnings

In [79]:
import time
start = time.time()

In [80]:
rf_results = []

with warnings.catch_warnings():
    warnings.simplefilter("ignore")
    for user_id in wisdm.user_ids:
        test_set = wisdm.get_user_set(user_id)
        test_set = wisdm.remove_all_nan(test_set)

        test_labels = np.array([t.decode("utf-8") for t in test_set['class'].as_matrix()])
        test_features = test_set.as_matrix(columns=[test_set.columns[1:-1]])

        #print("%s labels, %s features" % (len(test_labels), len(test_features)))
        # training features & labels
        training_set = wisdm.data_df[wisdm.data_df['user'] != user_id]
        training_set = wisdm.remove_all_nan(training_set)
        training_labels = np.array([t.decode("utf-8") for t in training_set['class'].as_matrix()])
        training_features = training_set.as_matrix(columns=[test_set.columns[1:-1]])

        # normalize features
        scaler = StandardScaler().fit(training_features)
        scaled_train_x = scaler.transform(training_features)
        scaled_test_x = scaler.transform(test_features)

        clf = wisdm.weka_RF()
        clf.fit(scaled_train_x, training_labels)
        predictions = clf.predict(scaled_test_x)

        score = accuracy_score(test_labels, predictions)
        print("Score for %s: %.3f" % (user_id, score))
        rf_results.append(score)

print("RF results : M=%.5f, SD=%.5f" % (np.mean(rf_results), np.std(rf_results)))

Score for 194: 0.447
Score for 998: 0.637
Score for 1097: 0.361
Score for 1104: 0.606
Score for 1117: 0.269
Score for 1205: 1.000
Score for 1238: 0.610
Score for 1246: 1.000
Score for 1247: 0.000
Score for 1253: 0.864
Score for 1269: 0.000
Score for 1274: 1.000
Score for 1276: 0.000
Score for 1277: 1.000
Score for 1280: 0.000
Score for 1319: 0.525
Score for 1320: 0.381
Score for 1477: 0.069
Score for 1480: 0.000
Score for 1491: 0.000
Score for 1511: 1.000
Score for 1512: 1.000
Score for 1518: 1.000
Score for 1531: 1.000
Score for 1554: 0.944
Score for 1559: 0.681
Score for 1603: 0.507
Score for 1676: 0.329
Score for 1679: 0.000
Score for 1683: 0.833
Score for 1696: 1.000
Score for 1703: 0.806
Score for 1707: 0.162
Score for 1723: 0.417
Score for 1724: 0.400
Score for 1726: 0.778
Score for 1742: 0.645
Score for 1745: 0.000
Score for 1750: 0.167
Score for 1757: 1.000
Score for 1758: 0.800
Score for 1759: 0.724
Score for 1761: 0.545
Score for 1763: 0.000
Score for 1774: 0.724
Score for 17

In [81]:
finish = time.time()
print("Took about %s seconds" % (finish - start))

TypeError: unsupported operand type(s) for -: 'str' and 'float'

# Cross-Validation with exact number of data points

### Experiment Attributes : 
* amount of training set from individual end user
* amount of training set from impersonal data (other users)
    * "ALL" all other data
    * "closest cluster" only data from the closest cluster
    * "furthest cluster" only data from the furthest cluster
    * "All - furthest cluster" all other data EXCEPT data from furthest cluster
* test user id
* algorithm
* algorithm parameters



In [4]:
def personal_model(active_features, active_labels, test_features, test_labels):
    scaler = StandardScaler().fit(active_features)
    scaled_train_x = scaler.transform(active_features)
    scaled_test_x = scaler.transform(test_features)

    rfc_clf = wisdm.weka_RF()
    rfc_clf.fit(scaled_train_x, active_labels)
    predictions = rfc_clf.predict(scaled_test_x)
    score = accuracy_score(test_labels, predictions)
    return score

In [5]:
def universal_model(universal_features, universal_labels, test_features, test_labels):
    scaler = StandardScaler().fit(universal_features)
    scaled_train_x = scaler.transform(universal_features)
    scaled_test_x = scaler.transform(test_features)

    rfc_clf = wisdm.weka_RF()
    rfc_clf.fit(scaled_train_x, universal_labels)
    predictions = rfc_clf.predict(scaled_test_x)
    score = accuracy_score(test_labels, predictions)

    return score

In [14]:
def universal_plus_personal_model(personal_features, personal_labels,
                                  universal_features, universal_labels,
                                  test_features, test_labels):
    personal_plus_universal_features = np.vstack((personal_features, universal_features))
    personal_plus_universal_labels = np.hstack((personal_labels, universal_labels))

    scaler = StandardScaler().fit(personal_plus_universal_features)
    scaled_train_x = scaler.transform(personal_plus_universal_features)
    scaled_test_x = scaler.transform(test_features)

    rfc_clf = wisdm.weka_RF()

    rfc_clf.fit(scaled_train_x, personal_plus_universal_labels)
    predictions = rfc_clf.predict(scaled_test_x)
    score = accuracy_score(test_labels, predictions)
    return score

In [18]:
def cluster_plus_personal_model(personal_features, personal_labels,
                                  universal_features, universal_labels,
                                  test_features, test_labels, KM):
    cluster_predictions = KM.predict(personal_features)
    closest_cluster = mode(cluster_predictions).mode[0]

    cluster_data_indeces = [i for i in range(len(clusters)) if clusters[i] == closest_cluster]
    cluster_features = universal_features[cluster_data_indeces]
    cluster_labels = universal_labels[cluster_data_indeces]

    training_features = np.vstack((personal_features, cluster_features))
    training_labels = np.hstack((personal_labels, cluster_labels))

    scaler = StandardScaler().fit(training_features)
    scaled_train_x = scaler.transform(training_features)
    scaled_test_x = scaler.transform(test_features)

    rfc_clf = wisdm.weka_RF()

    rfc_clf.fit(scaled_train_x, training_labels)
    predictions = rfc_clf.predict(scaled_test_x)
    score = accuracy_score(test_labels, predictions)
    return score

In [28]:
from collections import Counter

In [43]:
training_sizes = [10,20,30,40,50,60,70,80,90,100]

scores = []
err = None
with warnings.catch_warnings():
    warnings.simplefilter("ignore")
    for ind, user_id in enumerate(wisdm.user_ids):
        user_scores_df = []
        print("Running user #%s: %s" % (ind, user_id))
        personal_set = wisdm.get_user_set(user_id)
        personal_set = wisdm.remove_all_nan(personal_set)

        personal_labels = np.array([t.decode("utf-8") for t in personal_set['class'].as_matrix()])
        personal_features = personal_set.as_matrix(columns=[personal_set.columns[1:-1]])
        
        # What is the distribution of labels for this participant?
        personal_labels_distribution = Counter(personal_labels)
        print("\tHas %s labels : " % len(personal_labels))
        for label_key, number in personal_labels_distribution.items():
            print("\t\t%s:%s" % (label_key, number))
        print("\n")
        # training features & labels
        universal_set = wisdm.data_df[wisdm.data_df['user'] != user_id]
        universal_set = wisdm.remove_all_nan(universal_set)
        universal_labels = np.array([t.decode("utf-8") for t in universal_set['class'].as_matrix()])
        universal_features = universal_set.as_matrix(columns=[universal_set.columns[1:-1]])
        
        # get k-means clusters
        number_of_clusters = 4 # the higher this number is, the smaller we should expect each cluster to be

        KM = KMeans(n_clusters=number_of_clusters)
        clusters = KM.fit_predict(universal_features)
        
        k = 10
        
        skf = StratifiedKFold(n_splits=k)
        
        k_run = 0
        for active_index, test_index in skf.split(personal_features, personal_labels):
            print("\tRunning Fold #%s\n" % k_run)
            # data set available for active labeling from the individual
            all_active_features = personal_features[active_index]
            all_active_labels = personal_labels[active_index]


            # held out test set from individual
            test_features = personal_features[test_index]
            test_labels = personal_labels[test_index]

            # iterate through size of training data
            for training_size in training_sizes:
                # initialize score holders
                personal_model_scores = []
                universal_model_scores = []
                personal_plus_all_scores = []
                personal_plus_cluster_scores = []

                # run universal model
                universal_model_score = universal_model(universal_features, universal_labels,
                                                        test_features, test_labels)
                universal_model_scores.append(universal_model_score)

                sss = StratifiedShuffleSplit(n_splits=5, train_size=training_size, test_size=6)

                splits = sss.split(all_active_features, all_active_labels)

                try:
                    for split_num, split_tup in enumerate(splits):
                        sampled_active_index, __ = split_tup
                        sampled_active_features = personal_features[sampled_active_index]
                        sampled_active_labels = personal_labels[sampled_active_index]

                        # run personal model
                        personal_score = personal_model(sampled_active_features, sampled_active_labels, test_features, test_labels)
                        personal_model_scores.append(personal_score)

                        # run personal + universal
                        personal_plus_all_score = universal_plus_personal_model(sampled_active_features, sampled_active_labels,
                                                                                universal_features, universal_labels,
                                                                                test_features, test_labels)
                        personal_plus_all_scores.append(personal_plus_all_score)

                        # run personal + cluster
                        personal_plus_cluster_score = cluster_plus_personal_model(sampled_active_features, sampled_active_labels,
                                                                                universal_features, universal_labels,
                                                                                test_features, test_labels, KM)
                        personal_plus_cluster_scores.append(personal_plus_cluster_score)
                except ValueError as ve:
                    print("Error with training size during split #%s" % split_num)
                    print("Message : %s" % ve.args[0])
                    err = ve
                    if "Reduce test_size and/or train_size" in ve.args[0]:
                        print("continuing...")
                        continue
                    elif "should be smaller than the number of samples" in ve.args[0]:
                        print("continuing...")
                        continue
                    elif "The least populated class in y has only 1 member" in ve.args[0]:
                        print("continuing...")
                        continue
                    else:
                        raise(ve)

                row = {"test user" : user_id,
                       "k-run" : k_run,
                   "classifier" : "RF with Wiki Parameters",
                   "personal training data" : training_size,
                   "personal score Mean" : np.mean(personal_model_scores),
                   "personal score STD" : np.std(personal_model_scores),
                   "impersonal score Mean" : np.mean(universal_model_scores),
                   "impersonal score STD" : np.std(universal_model_scores),
                   "personal + impersonal score Mean" : np.mean(personal_plus_all_scores),
                   "personal + impersonal score STD" : np.std(personal_plus_all_scores),
                   "personal + cluster score Mean" : np.mean(personal_plus_cluster_scores),
                   "personal + cluster score STD" : np.std(personal_plus_cluster_scores)
                   }
                print("\tamount of personal data : %s row" % training_size)
                print("\tpersonal model score : M=%.3f, SD=%.3f" % (row["personal score Mean"], row["personal score STD"]))
                print("\tuniversal model score : M=%.3f, SD=%.3f" % (row["impersonal score Mean"], row["impersonal score STD"]))
                print("\tpersonal + ALL universal : M=%.3f, SD=%.3f" % (row["personal + impersonal score Mean"], row["personal + impersonal score STD"]))
                print("\tpersonal + CLUSTER universal : M=%.3f, SD=%.3f" % (row["personal + cluster score Mean"], row["personal + cluster score STD"]))
                print("\n")
                scores.append(row)
                user_scores_df.append(row)
            k_run += 1
        user_scores_df = pd.DataFrame(user_scores_df)
        user_scores_df.to_pickle("./results/experiment_08-17/"+user_id+".pickle")

scores_df = pd.DataFrame(scores)

Running user #0: 33
	Has 149 labels : 
		Jogging:15
		Walking:74
		Upstairs:12
		Downstairs:24
		Standing:7
		Sitting:17


	Running Fold #0

	amount of personal data : 10 row
	personal model score : M=0.544, SD=0.065
	universal model score : M=0.722, SD=0.000
	personal + ALL universal : M=0.722, SD=0.050
	personal + CLUSTER universal : M=0.756, SD=0.057


	amount of personal data : 20 row
	personal model score : M=0.633, SD=0.027
	universal model score : M=0.722, SD=0.000
	personal + ALL universal : M=0.722, SD=0.035
	personal + CLUSTER universal : M=0.756, SD=0.027


	amount of personal data : 30 row
	personal model score : M=0.689, SD=0.044
	universal model score : M=0.722, SD=0.000
	personal + ALL universal : M=0.756, SD=0.044
	personal + CLUSTER universal : M=0.789, SD=0.054


	amount of personal data : 40 row
	personal model score : M=0.767, SD=0.065
	universal model score : M=0.722, SD=0.000
	personal + ALL universal : M=0.811, SD=0.090
	personal + CLUSTER universal : M=0.878, SD

	amount of personal data : 80 row
	personal model score : M=0.859, SD=0.029
	universal model score : M=0.765, SD=0.000
	personal + ALL universal : M=0.941, SD=0.000
	personal + CLUSTER universal : M=0.965, SD=0.029


	amount of personal data : 90 row
	personal model score : M=0.835, SD=0.058
	universal model score : M=0.824, SD=0.000
	personal + ALL universal : M=0.941, SD=0.053
	personal + CLUSTER universal : M=0.965, SD=0.047


	amount of personal data : 100 row
	personal model score : M=0.871, SD=0.024
	universal model score : M=0.765, SD=0.000
	personal + ALL universal : M=0.965, SD=0.047
	personal + CLUSTER universal : M=1.000, SD=0.000


	Running Fold #4

	amount of personal data : 10 row
	personal model score : M=0.587, SD=0.107
	universal model score : M=0.800, SD=0.000
	personal + ALL universal : M=0.893, SD=0.033
	personal + CLUSTER universal : M=0.920, SD=0.027


	amount of personal data : 20 row
	personal model score : M=0.733, SD=0.073
	universal model score : M=0.933, SD=

	amount of personal data : 60 row
	personal model score : M=0.933, SD=0.033
	universal model score : M=0.750, SD=0.000
	personal + ALL universal : M=0.933, SD=0.062
	personal + CLUSTER universal : M=0.933, SD=0.033


	amount of personal data : 70 row
	personal model score : M=0.983, SD=0.033
	universal model score : M=0.750, SD=0.000
	personal + ALL universal : M=0.933, SD=0.033
	personal + CLUSTER universal : M=0.983, SD=0.033


	amount of personal data : 80 row
	personal model score : M=0.933, SD=0.033
	universal model score : M=0.833, SD=0.000
	personal + ALL universal : M=0.900, SD=0.062
	personal + CLUSTER universal : M=0.933, SD=0.033


	amount of personal data : 90 row
	personal model score : M=0.950, SD=0.041
	universal model score : M=0.750, SD=0.000
	personal + ALL universal : M=0.967, SD=0.041
	personal + CLUSTER universal : M=0.950, SD=0.041


	amount of personal data : 100 row
	personal model score : M=0.950, SD=0.041
	universal model score : M=0.750, SD=0.000
	personal + 

	amount of personal data : 40 row
	personal model score : M=0.964, SD=0.045
	universal model score : M=0.455, SD=0.000
	personal + ALL universal : M=0.945, SD=0.073
	personal + CLUSTER universal : M=0.945, SD=0.073


	amount of personal data : 50 row
	personal model score : M=0.964, SD=0.045
	universal model score : M=0.455, SD=0.000
	personal + ALL universal : M=0.909, SD=0.081
	personal + CLUSTER universal : M=0.909, SD=0.081


	amount of personal data : 60 row
	personal model score : M=1.000, SD=0.000
	universal model score : M=0.364, SD=0.000
	personal + ALL universal : M=0.982, SD=0.036
	personal + CLUSTER universal : M=1.000, SD=0.000


	amount of personal data : 70 row
	personal model score : M=1.000, SD=0.000
	universal model score : M=0.545, SD=0.000
	personal + ALL universal : M=0.982, SD=0.036
	personal + CLUSTER universal : M=1.000, SD=0.000


	amount of personal data : 80 row
	personal model score : M=1.000, SD=0.000
	universal model score : M=0.545, SD=0.000
	personal + A

	amount of personal data : 40 row
	personal model score : M=0.920, SD=0.040
	universal model score : M=0.300, SD=0.000
	personal + ALL universal : M=0.860, SD=0.102
	personal + CLUSTER universal : M=0.940, SD=0.080


	amount of personal data : 50 row
	personal model score : M=0.960, SD=0.049
	universal model score : M=0.400, SD=0.000
	personal + ALL universal : M=0.920, SD=0.040
	personal + CLUSTER universal : M=0.980, SD=0.040


	amount of personal data : 60 row
	personal model score : M=1.000, SD=0.000
	universal model score : M=0.300, SD=0.000
	personal + ALL universal : M=0.980, SD=0.040
	personal + CLUSTER universal : M=0.980, SD=0.040


	amount of personal data : 70 row
	personal model score : M=1.000, SD=0.000
	universal model score : M=0.400, SD=0.000
	personal + ALL universal : M=1.000, SD=0.000
	personal + CLUSTER universal : M=1.000, SD=0.000


	amount of personal data : 80 row
	personal model score : M=1.000, SD=0.000
	universal model score : M=0.300, SD=0.000
	personal + A

...

	amount of personal data : 80 row
	personal model score : M=0.886, SD=0.057
	universal model score : M=0.857, SD=0.000
	personal + ALL universal : M=0.929, SD=0.000
	personal + CLUSTER universal : M=0.900, SD=0.035


	amount of personal data : 90 row
	personal model score : M=0.900, SD=0.035
	universal model score : M=0.857, SD=0.000
	personal + ALL universal : M=0.929, SD=0.000
	personal + CLUSTER universal : M=0.886, SD=0.057


	amount of personal data : 100 row
	personal model score : M=0.914, SD=0.029
	universal model score : M=0.857, SD=0.000
	personal + ALL universal : M=0.929, SD=0.000
	personal + CLUSTER universal : M=0.929, SD=0.000


	Running Fold #3

	amount of personal data : 10 row
	personal model score : M=0.757, SD=0.057
	universal model score : M=0.857, SD=0.000
	personal + ALL universal : M=0.829, SD=0.035
	personal + CLUSTER universal : M=0.843, SD=0.053


	amount of personal data : 20 row
	personal model score : M=0.786, SD=0.000
	universal model score : M=0.857, SD=

	amount of personal data : 60 row
	personal model score : M=0.818, SD=0.000
	universal model score : M=0.818, SD=0.000
	personal + ALL universal : M=0.818, SD=0.000
	personal + CLUSTER universal : M=0.818, SD=0.000


	amount of personal data : 70 row
	personal model score : M=0.836, SD=0.036
	universal model score : M=0.818, SD=0.000
	personal + ALL universal : M=0.818, SD=0.000
	personal + CLUSTER universal : M=0.818, SD=0.000


	amount of personal data : 80 row
	personal model score : M=0.855, SD=0.045
	universal model score : M=0.818, SD=0.000
	personal + ALL universal : M=0.818, SD=0.000
	personal + CLUSTER universal : M=0.818, SD=0.000


	amount of personal data : 90 row
	personal model score : M=0.818, SD=0.000
	universal model score : M=0.818, SD=0.000
	personal + ALL universal : M=0.818, SD=0.000
	personal + CLUSTER universal : M=0.818, SD=0.000


	amount of personal data : 100 row
	personal model score : M=0.836, SD=0.036
	universal model score : M=0.818, SD=0.000
	personal + 

	amount of personal data : 30 row
	personal model score : M=0.809, SD=0.045
	universal model score : M=0.864, SD=0.000
	personal + ALL universal : M=0.873, SD=0.045
	personal + CLUSTER universal : M=0.818, SD=0.029


	amount of personal data : 40 row
	personal model score : M=0.855, SD=0.045
	universal model score : M=0.818, SD=0.000
	personal + ALL universal : M=0.900, SD=0.018
	personal + CLUSTER universal : M=0.873, SD=0.018


	amount of personal data : 50 row
	personal model score : M=0.836, SD=0.022
	universal model score : M=0.864, SD=0.000
	personal + ALL universal : M=0.891, SD=0.022
	personal + CLUSTER universal : M=0.845, SD=0.022


	amount of personal data : 60 row
	personal model score : M=0.864, SD=0.050
	universal model score : M=0.909, SD=0.000
	personal + ALL universal : M=0.927, SD=0.022
	personal + CLUSTER universal : M=0.882, SD=0.036


	amount of personal data : 70 row
	personal model score : M=0.891, SD=0.046
	universal model score : M=0.864, SD=0.000
	personal + A

	amount of personal data : 10 row
	personal model score : M=0.850, SD=0.000
	universal model score : M=0.800, SD=0.000
	personal + ALL universal : M=0.850, SD=0.000
	personal + CLUSTER universal : M=0.860, SD=0.037


	amount of personal data : 20 row
	personal model score : M=0.850, SD=0.000
	universal model score : M=0.800, SD=0.000
	personal + ALL universal : M=0.870, SD=0.024
	personal + CLUSTER universal : M=0.890, SD=0.020


	amount of personal data : 30 row
	personal model score : M=0.850, SD=0.000
	universal model score : M=0.850, SD=0.000
	personal + ALL universal : M=0.870, SD=0.024
	personal + CLUSTER universal : M=0.870, SD=0.024


	amount of personal data : 40 row
	personal model score : M=0.850, SD=0.000
	universal model score : M=0.900, SD=0.000
	personal + ALL universal : M=0.890, SD=0.020
	personal + CLUSTER universal : M=0.870, SD=0.024


	amount of personal data : 50 row
	personal model score : M=0.850, SD=0.000
	universal model score : M=0.850, SD=0.000
	personal + A

	amount of personal data : 90 row
	personal model score : M=0.889, SD=0.000
	universal model score : M=0.944, SD=0.000
	personal + ALL universal : M=0.967, SD=0.027
	personal + CLUSTER universal : M=0.933, SD=0.022


	amount of personal data : 100 row
	personal model score : M=0.889, SD=0.000
	universal model score : M=0.889, SD=0.000
	personal + ALL universal : M=0.956, SD=0.022
	personal + CLUSTER universal : M=0.944, SD=0.000


	Running Fold #8

	amount of personal data : 10 row
	personal model score : M=0.889, SD=0.000
	universal model score : M=0.944, SD=0.000
	personal + ALL universal : M=0.956, SD=0.022
	personal + CLUSTER universal : M=0.922, SD=0.027


	amount of personal data : 20 row
	personal model score : M=0.889, SD=0.000
	universal model score : M=0.944, SD=0.000
	personal + ALL universal : M=0.933, SD=0.022
	personal + CLUSTER universal : M=0.922, SD=0.027


	amount of personal data : 30 row
	personal model score : M=0.889, SD=0.000
	universal model score : M=0.944, SD=

# Visualize results

In [64]:
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
from plotly.graph_objs import *

In [56]:
results = []
for user_id in wisdm.user_ids:
    user_results_df = pd.read_pickle("./results/experiment_08-17/"+user_id+".pickle")
    results.append(user_results_df)
        
results_df = pd.concat(results).reset_index(drop=True)


In [111]:
results_df.describe()

impersonal score Mean  impersonal score STD        k-run  \
count            3203.000000                3203.0  3203.000000   
mean                0.759894                   0.0     4.542304   
std                 0.189597                   0.0     2.860652   
min                 0.000000                   0.0     0.000000   
25%                 0.733333                   0.0     2.000000   
50%                 0.800000                   0.0     5.000000   
75%                 0.866667                   0.0     7.000000   
max                 1.000000                   0.0     9.000000   

       personal + cluster score Mean  personal + cluster score STD  \
count                    3203.000000                   3203.000000   
mean                        0.886941                      0.038746   
std                         0.083594                      0.030328   
min                         0.433333                      0.000000   
25%                         0.833333                      0.023529   
50%                         0.894118                      0.036364   
75%                         0.953846                      0.053452   
max                         1.000000                      0.277010   

       personal + impersonal score Mean  personal + impersonal score STD  \
count                       3203.000000                     3.203000e+03   
mean                           0.895210                     3.566705e-02   
std                            0.085486                     3.103443e-02   
min                            0.288889                     0.000000e+00   
25%                            0.844444                     1.110223e-16   
50%                            0.907692                     3.333333e-02   
75%                            0.960000                     5.000000e-02   
max                            1.000000                     3.431877e-01   

       personal score Mean  personal score STD  personal training data  
count          3203.000000        3.203000e+03             3203.000000  
mean              0.880926        3.728103e-02               52.425851  
std               0.088196        3.156351e-02               28.067305  
min               0.500000        0.000000e+00               10.000000  
25%               0.830385        1.110223e-16               30.000000  
50%               0.890909        3.499271e-02               50.000000  
75%               0.942857        5.345225e-02               80.000000  
max               1.000000        2.328409e-01              100.000000

In [109]:
personal_means = {}
personal_plus_universal_means = {}
personal_plus_cluster_means = {}
universal_means = results_df['impersonal score Mean']

for ts in training_sizes:
    personal_scores = results_df[results_df['personal training data'] == ts]['personal score Mean']
    personal_means[ts] = personal_scores
    
    personal_plus_universal_scores = results_df[results_df['personal training data'] == ts]['personal + impersonal score Mean']
    personal_plus_universal_means[ts] = personal_plus_universal_scores
    
    personal_plus_cluster_scores = results_df[results_df['personal training data'] == ts]['personal + cluster score Mean']
    personal_plus_cluster_means[ts] = personal_plus_cluster_scores

In [110]:
universal_trace = Box(y=universal_means,
                      x=[0]*len(universal_means),
                      name="universal model",
                      boxpoints='suspectedoutliers',
                      )

data = [universal_trace]

personal_x = []
personal_plus_universal_x = []
personal_plus_cluster_x = []

personal_means_all = []
personal_plus_universal_means_all = []
personal_plus_cluster_means_all = []

for ts in training_sizes:
    personal_means_all += personal_means[ts].tolist()
    personal_x += [ts] * len(personal_means[ts])
    
    personal_plus_universal_means_all += personal_plus_universal_means[ts].tolist()
    personal_plus_universal_x += [ts] *len(personal_plus_universal_means[ts])
    
    personal_plus_cluster_means_all += personal_plus_cluster_means[ts].tolist()
    personal_plus_cluster_x += [ts] * len(personal_plus_cluster_means[ts])

personal_trace = Box(y=personal_means_all,
                     x=personal_x,
                     name="Personal",
                     boxpoints="suspectedoutliers")

data.append(personal_trace)

personal_plus_universal_trace = Box(y=personal_plus_universal_means_all,
                                    x=personal_plus_universal_x,
                                    name="Personal + Universal",
                                    boxpoints="suspectedoutliers")

data.append(personal_plus_universal_trace)

personal_plus_cluster_trace = Box(y=personal_plus_cluster_means_all,
                                    x=personal_plus_cluster_x,
                                    name="Personal + Cluster",
                                    boxpoints="suspectedoutliers")

data.append(personal_plus_cluster_trace)

layout = Layout(showlegend=True, boxmode='group')
fig = Figure(data=data, layout=layout)

iplot(fig, filename="boxplots_of_wisdm_models")

## By user

In [136]:
def plotScoresByUser(user_id):
    personal_means = {}
    personal_plus_universal_means = {}
    personal_plus_cluster_means = {}
    universal_means = results_df['impersonal score Mean']

    for ts in training_sizes:
        personal_scores = results_df[(results_df['personal training data'] == ts) & \
                                     (results_df['test user'] == user_id)]['personal score Mean']
        personal_means[ts] = personal_scores

        personal_plus_universal_scores = results_df[(results_df['personal training data'] == ts) & \
                                     (results_df['test user'] == user_id)]['personal + impersonal score Mean']
        personal_plus_universal_means[ts] = personal_plus_universal_scores

        personal_plus_cluster_scores = results_df[(results_df['personal training data'] == ts) & \
                                     (results_df['test user'] == user_id)]['personal + cluster score Mean']
        personal_plus_cluster_means[ts] = personal_plus_cluster_scores
    
    
    universal_trace = Box(y=universal_means,
                      x=[0]*len(universal_means),
                      name="universal model",
                      boxpoints='suspectedoutliers',
                      )

    data = [universal_trace]

    personal_x = []
    personal_plus_universal_x = []
    personal_plus_cluster_x = []

    personal_means_all = []
    personal_plus_universal_means_all = []
    personal_plus_cluster_means_all = []

    for ts in training_sizes:
        personal_means_all += personal_means[ts].tolist()
        personal_x += [ts] * len(personal_means[ts])

        personal_plus_universal_means_all += personal_plus_universal_means[ts].tolist()
        personal_plus_universal_x += [ts] *len(personal_plus_universal_means[ts])

        personal_plus_cluster_means_all += personal_plus_cluster_means[ts].tolist()
        personal_plus_cluster_x += [ts] * len(personal_plus_cluster_means[ts])

    personal_trace = Box(y=personal_means_all,
                         x=personal_x,
                         name="Personal",
                         boxpoints="suspectedoutliers")

    data.append(personal_trace)

    personal_plus_universal_trace = Box(y=personal_plus_universal_means_all,
                                        x=personal_plus_universal_x,
                                        name="Personal + Universal",
                                        boxpoints="suspectedoutliers")

    data.append(personal_plus_universal_trace)

    personal_plus_cluster_trace = Box(y=personal_plus_cluster_means_all,
                                        x=personal_plus_cluster_x,
                                        name="Personal + Cluster",
                                        boxpoints="suspectedoutliers")

    data.append(personal_plus_cluster_trace)

    layout = Layout(showlegend=True, boxmode='group')
    fig = Figure(data=data, layout=layout)

    iplot(fig, filename="boxplots_of_wisdm_models")

In [137]:
plotScoresByUser(wisdm.user_ids[0])

In [138]:
plotScoresByUser(wisdm.user_ids[1])

In [139]:
plotScoresByUser(wisdm.user_ids[2])

In [140]:
plotScoresByUser(wisdm.user_ids[3])

In [142]:
plotScoresByUser(wisdm.user_ids[4])

# Component Analysis

In [112]:
from sklearn.decomposition import PCA

In [117]:
import colorlover as cl

In [119]:
from IPython.display import HTML

In [131]:
pca = PCA(n_components=2)

universal_set = wisdm.data_df
universal_set = wisdm.remove_all_nan(universal_set)
universal_labels = np.array([t.decode("utf-8") for t in universal_set['class'].as_matrix()])
universal_features = universal_set.as_matrix(columns=[universal_set.columns[1:-1]])

activity_classes = list(set(universal_labels))

qualitative_colors = cl.scales['6']['qual']['Set1']

activity_colors = {activity_classes[i] : color for i,color in enumerate(qualitative_colors)}

features_pca_space = pca.fit(universal_features).transform(universal_features)

# Percentage of variance explained for each components
print('explained variance ratio (first two components): %s'
      % str(pca.explained_variance_ratio_))

trace = Scatter(x=[d[0] for d in features_pca_space],
                y=[d[1] for d in features_pca_space],
                mode='markers',
                marker=dict(color=[activity_colors[activity] for activity in universal_labels],
                            opacity=0.5))
data = [trace]
iplot(data,filename="pca")

explained variance ratio (first two components): [ 0.45996046  0.31853441]


In [128]:
HTML(cl.to_html(cl.scales['6']['qual']['Set1']))

In [130]:
for activity in activity_classes:
    print(activity)

Downstairs
Jogging
Sitting
Walking
Upstairs
Standing


In [133]:
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis

lda = LinearDiscriminantAnalysis(n_components=2)

features_lda_space = lda.fit(universal_features, universal_labels).transform(universal_features)

trace = Scatter(x=[d[0] for d in features_lda_space],
                y=[d[1] for d in features_lda_space],
                mode='markers',
                marker=dict(color=[activity_colors[activity] for activity in universal_labels],
                            opacity=0.7))
data = [trace]
iplot(data,filename="lda")

/Users/scottcambo/.virtualenvs/machinelearning/lib/python3.6/site-packages/sklearn/discriminant_analysis.py:387: UserWarning:

Variables are collinear.

